In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, KFold, StratifiedKFold,GridSearchCV
from sklearn.metrics import roc_auc_score, recall_score,precision_score, fbeta_score, f1_score, accuracy_score, precision_recall_curve, roc_curve,auc
from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler
from imblearn.pipeline import Pipeline
from imblearn.pipeline import Pipeline as imbpipeline
from sklearn.preprocessing import MinMaxScaler,OneHotEncoder, StandardScaler
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import make_scorer, fbeta_score, classification_report, accuracy_score ,confusion_matrix
from xgboost import XGBClassifier
import pickle
import collections
from joblib import dump, load

### import data

In [2]:
X_train= pd.read_pickle('X_train.pkl')
y_train= pd.read_pickle('y_train.pkl')
X_test= pd.read_pickle('X_test.pkl')
y_test= pd.read_pickle('y_test.pkl')

column_names = X_train.columns

In [3]:
# We need to convert the labels {-1,+1} --> {0,+1} becasue XGboost expects {0,+1} only

y_train = y_train.map({-1: 0, 1: 1})
y_test = y_test.map({-1: 0, 1: 1})  

In [4]:
counter = collections.Counter(y_train)
print(counter)
counter = collections.Counter(y_test)
print(counter)

Counter({0: 1398, 1: 11})
Counter({0: 350, 1: 3})


In [5]:
X_train

Cation_Mass  cat:nAcid  cat:nBase  cat:SpAbs_A  cat:SpMax_A  \
592        97.138          0          1     8.917367     2.151538   
839       171.283          0          1    13.592431     2.256190   
829        97.140          0          1     8.428639     2.214320   
1203      195.285          0          1    17.187439     2.258502   
1683      483.856          0          1    40.978881     2.308870   
...           ...        ...        ...          ...          ...   
523       150.240          0          1    13.725227     2.205946   
654       111.164          0          1     9.910095     2.224503   
506       139.218          0          1    12.426800     2.236324   
1611      217.351          0          1    16.806253     2.250430   
1336      270.516          0          1    22.514725     2.283998   

      cat:SpDiam_A  cat:SpAD_A  cat:SpMAD_A  cat:LogEE_A  cat:VE1_A  ...  \
592       4.096394    8.917367     1.273910     2.849625   2.534374  ...   
839       4.345820   13.592431     1.235676     3.281898   2.869873  ...   
829       4.214320    8.428639     1.204091     2.862063   2.544200  ...   
1203      4.517004   17.187439     1.227674     3.514325   3.262195  ...   
1683      4.617740   40.978881     1.241784     4.323254   3.607368  ...   
...            ...         ...          ...          ...        ...  ...   
523       4.411892   13.725227     1.247748     3.278326   3.019439  ...   
654       4.194610    9.910095     1.238762     2.984531   2.668822  ...   
506       4.251712   12.426800     1.242680     3.191982   2.830660  ...   
1611      4.500860   16.806253     1.200447     3.468888   3.086756  ...   
1336      4.567996   22.514725     1.184986     3.782481   3.560866  ...   

      an:SRW09   an:SRW10  an:TSRW10       an:MW     an:AMW  an:WPath  \
592   0.000000   9.037771  36.999431  148.952573  18.619072        58   
839   0.000000   9.921769  47.846479  279.917842  18.661189       340   
829   0.000000   9.921769  47.846479  279.917842  18.661189       340   
1203  0.000000   9.921769  47.846479  279.917842  18.661189       340   
1683  7.727094  10.186145  74.161904  311.073242   8.887807      1174   
...        ...        ...        ...         ...        ...       ...   
523   0.000000   6.192362  25.583106   66.009771  13.201954        20   
654   0.000000   7.625107  29.418928   94.980839  11.872605        16   
506   0.000000   8.466531  34.219913  112.985587  16.140798        42   
1611  0.000000   7.989899  31.665095  110.975753  12.330639        28   
1336  0.000000   6.834109  27.254130   73.029503   7.302950        18   

      an:WPol  an:Zagreb1  an:Zagreb2  an:mZagreb2  
592         9        38.0        40.0     1.562500  
839        24        78.0        88.0     2.875000  
829        24        78.0        88.0     2.875000  
1203       24        78.0        88.0     2.875000  
1683       36       128.0       154.0     4.944444  
...       ...         ...         ...          ...  
523         2        14.0        12.0     1.500000  
654         0        20.0        16.0     1.000000  
506         6        30.0        30.0     1.500000  
1611        3        24.0        22.0     1.375000  
1336        2        16.0        14.0     1.333333  

[1409 rows x 1762 columns]

### Define functions to train and evaluate the model on the training and testing sets

In [6]:
# function to training models

def train_model(model,params,refit_score,X,y):
    '''
    Train model with CV and grid search.
            Parameters:
                    model: model's initialization
                    params : model's hyperparametres
                    X, y : Data to train
            Returns:
                    grid search results
    '''

    pipeline = imbpipeline(steps = [
                                ['smote_over', SMOTE(random_state=11,sampling_strategy=0.1)],
                                #The original paper suggested combining SMOTE with random undersampling of the majority class
                                ['smote_under',RandomUnderSampler(sampling_strategy=0.5)],
                                ('scaler', StandardScaler()),                                   # Feature scaling
                                ['classifier',model]])



    # Create a scorer for F-beta where beta=2
    f2_scorer = make_scorer(fbeta_score, beta=2)
    
    custom_precision_scorer = make_scorer(precision_score, zero_division=0)
    
    grid_search = GridSearchCV(estimator=pipeline,
                           param_grid=params,
                           scoring={    'precision': custom_precision_scorer,
                                        'recall': 'recall',
                                        'f1_score': "f1"},
                           refit = refit_score,
                           cv=StratifiedKFold(n_splits=3,shuffle=True, random_state=11),
                           verbose=3,
                           n_jobs=-1)
    
        
    
    

    return grid_search.fit(X,y)


# function to evaluate model

def evaluate_model (model_name, grid_search_results, final_result):
    '''
    Evaluate the model.
            Parameters:
                    model_name
                    grid_search_results
                    final_result: empty DF to stock results
            Returns:
                    final_result : DF filles with the results
    '''
    results_data = [model_name]
    maxPRECISION = max(grid_search_results.cv_results_["mean_test_precision"])
    maxRECALL = max(grid_search_results.cv_results_["mean_test_recall"])
    maxF1 = max(grid_search_results.cv_results_["mean_test_f1_score"])

    
    results_data.append(maxPRECISION)
    results_data.append(maxRECALL)
    results_data.append(maxF1)


    idx = grid_search_results.cv_results_["mean_test_precision"].tolist().index(maxPRECISION)
    results_data.append(grid_search_results.cv_results_['params'][idx])
    
    idx = grid_search_results.cv_results_["mean_test_recall"].tolist().index(maxRECALL)
    results_data.append(grid_search_results.cv_results_['params'][idx])
    

    idx = grid_search_results.cv_results_["mean_test_f1_score"].tolist().index(maxF1)
    results_data.append(grid_search_results.cv_results_['params'][idx])

        

    final_result.loc[len(final_result)]=results_data
    return final_result


# function to evaluate model

def evaluate_model_on_test (model_name, X_test,y_test,classifier, final_result):
    '''
    Evaluate the model on test set.
            Parameters:
                    model_name
                    X_test,y_test : Data
                    classifier : The best model chooses
                    final_result: empty DF to stock results
            Returns:
                    final_result : DF filles with the results
    '''

    results_data = [model_name]
    
    precision_test = precision_score(y_test,classifier.predict(X_test))
    recall_test = recall_score(y_test,classifier.predict(X_test))
    f1_test = f1_score(y_test, classifier.predict(X_test))
    #f2_test = fbeta_score(y_test, classifier.predict(X_test), beta=2)
  

    
    results_data.append(precision_test)
    results_data.append(recall_test)
    results_data.append(f1_test)
    final_result.loc[len(final_result)]=results_data

    #maxPRECISION = max(grid_search_results.cv_results_["mean_test_precision"])
    return final_result

In [7]:
# DF to stocks results
final_results = pd.DataFrame(columns=["name","PRECISION","RECALL","F1 score","BestParamsM1","BestParamsM2","BestParamsM3"])

In [8]:
refit_score='precision'

### 1. Logistic regression

In [9]:
%time
model = LogisticRegression(random_state=11,max_iter=1000,solver='liblinear')
params = {    'smote_over__k_neighbors': [2,3,4],  # Parameters for SMOTE oversampling
            'smote_over__sampling_strategy': [0.1,0.2, 0.3, 0.4],
            'smote_under__sampling_strategy': [0.3,0.4, 0.5, 0.6],
            'classifier__penalty' : ['l1', 'l2'], 
          'classifier__C' : [0.001, 0.01, 0.1, 1, 10, 100, 1000],
          'smote_over__k_neighbors': [2, 3, 4]}

search = train_model(model,params,refit_score,X_train,y_train)
final_results = evaluate_model("logistic",search, final_results)

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 2.38 µs


/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
126 fits failed out of a total of 2016.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
126 fits failed with the following error:
Traceback (most recent call last):
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/base.py", line 1151, in wrapper
    return fit_method(estimator, *args, **kwargs)
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/imblearn/pipeline.py", line 322, in fit
    Xt

In [10]:
# Save your model to a file
best_logreg_precision = search.best_estimator_
dump(best_logreg_precision, 'best_logreg_precision.joblib')

['best_logreg_precision.joblib']

In [11]:
y_pred = search.best_estimator_.predict(X_test)
# Calculate the accuracy on the test set
test_accuracy = accuracy_score(y_test, y_pred)
print(f'Test Set Accuracy: {test_accuracy * 100:.2f}%')
print("-------------")
# Print the classification report
y_pred = search.predict(X_test)
print(classification_report(y_test, y_pred))
cm = confusion_matrix(y_test, y_pred)
print("-------------")
# Print the confusion matrix
print("Confusion Matrix:")
print(cm)

Test Set Accuracy: 95.18%
-------------
              precision    recall  f1-score   support

           0       1.00      0.95      0.98       350
           1       0.11      0.67      0.19         3

    accuracy                           0.95       353
   macro avg       0.55      0.81      0.58       353
weighted avg       0.99      0.95      0.97       353

-------------
Confusion Matrix:
[[334  16]
 [  1   2]]


In [12]:
final_results

name  PRECISION    RECALL  F1 score  \
0  logistic   0.175676  0.916667  0.216667   

                                        BestParamsM1  \
0  {'classifier__C': 0.01, 'classifier__penalty':...   

                                        BestParamsM2  \
0  {'classifier__C': 0.001, 'classifier__penalty'...   

                                        BestParamsM3  
0  {'classifier__C': 0.01, 'classifier__penalty':...

In [13]:
best_params = final_results[final_results['name']=='logistic']['BestParamsM2']
print(best_params.values)

[{'classifier__C': 0.001, 'classifier__penalty': 'l2', 'smote_over__k_neighbors': 2, 'smote_over__sampling_strategy': 0.1, 'smote_under__sampling_strategy': 0.3}]


### 2. SVM

In [14]:
%time
model = SVC()

n_features= len(column_names)

params = {
    'smote_over__k_neighbors': [2,3,4],  # Parameters for SMOTE oversampling
    'smote_over__sampling_strategy': [0.1,0.2, 0.3, 0.4],
    'smote_under__sampling_strategy': [0.3,0.4, 0.5, 0.6],
    'classifier__C': [0.1, 1, 10, 20],
    'classifier__kernel': ['linear', 'rbf', 'poly'],
    'classifier__gamma': [0.1 * 1/n_features, 1/n_features, 10 * 1/n_features, 'scale'],
    'classifier__degree': [2, 3, 4]  # Relevant for 'poly' kernel
}


search = train_model(model,params,refit_score,X_train,y_train)
final_results = evaluate_model ("SVM",search, final_results)

CPU times: user 1 µs, sys: 0 ns, total: 1 µs
Wall time: 2.15 µs


/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
1296 fits failed out of a total of 20736.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
1296 fits failed with the following error:
Traceback (most recent call last):
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/base.py", line 1151, in wrapper
    return fit_method(estimator, *args, **kwargs)
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/imblearn/pipeline.py", line 322, in fit
   

In [15]:
search.best_estimator_

Pipeline(steps=[('smote_over',
                 SMOTE(k_neighbors=3, random_state=11, sampling_strategy=0.2)),
                ('smote_under', RandomUnderSampler(sampling_strategy=0.3)),
                ('scaler', StandardScaler()),
                ['classifier',
                 SVC(C=20, degree=4, gamma=0.0056753688989784334,
                     kernel='linear')]])

In [16]:
# Save your model to a file
best_svm_precision = search.best_estimator_
dump(best_svm_precision, 'best_svm_precision.joblib')

['best_svm_precision.joblib']

In [17]:
y_pred = search.best_estimator_.predict(X_test)
# Calculate the accuracy on the test set
test_accuracy = accuracy_score(y_test, y_pred)
print(f'Test Set Accuracy: {test_accuracy * 100:.2f}%')
print("-------------")
# Print the classification report
y_pred = search.predict(X_train)
print(classification_report(y_train, y_train))
cm = confusion_matrix(y_train, y_train)
print("-------------")
# Print the confusion matrix
print("Confusion Matrix - Training set:")
print(cm)


print("-------------")
# Print the classification report
y_pred = search.predict(X_test)
print(classification_report(y_test, y_pred))
cm = confusion_matrix(y_test, y_pred)
print("-------------")
# Print the confusion matrix
print("Confusion Matrix - Testing set:")
print(cm)

Test Set Accuracy: 97.73%
-------------
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      1398
           1       1.00      1.00      1.00        11

    accuracy                           1.00      1409
   macro avg       1.00      1.00      1.00      1409
weighted avg       1.00      1.00      1.00      1409

-------------
Confusion Matrix - Training set:
[[1398    0]
 [   0   11]]
-------------
              precision    recall  f1-score   support

           0       1.00      0.98      0.99       350
           1       0.22      0.67      0.33         3

    accuracy                           0.98       353
   macro avg       0.61      0.82      0.66       353
weighted avg       0.99      0.98      0.98       353

-------------
Confusion Matrix - Testing set:
[[343   7]
 [  1   2]]


In [18]:
final_results

name  PRECISION    RECALL  F1 score  \
0  logistic   0.175676  0.916667  0.216667   
1       SVM   0.410256  0.916667  0.370370   

                                        BestParamsM1  \
0  {'classifier__C': 0.01, 'classifier__penalty':...   
1  {'classifier__C': 20, 'classifier__degree': 4,...   

                                        BestParamsM2  \
0  {'classifier__C': 0.001, 'classifier__penalty'...   
1  {'classifier__C': 1, 'classifier__degree': 3, ...   

                                        BestParamsM3  
0  {'classifier__C': 0.01, 'classifier__penalty':...  
1  {'classifier__C': 1, 'classifier__degree': 2, ...

In [19]:
best_params = final_results[final_results['name']=='SVM']['BestParamsM2']
print(best_params.values)

[{'classifier__C': 1, 'classifier__degree': 3, 'classifier__gamma': 0.0005675368898978433, 'classifier__kernel': 'poly', 'smote_over__k_neighbors': 2, 'smote_over__sampling_strategy': 0.3, 'smote_under__sampling_strategy': 0.6}]


### 3.RF

In [20]:
model = RandomForestClassifier(n_estimators = 125)
params = {    'smote_over__k_neighbors': [2,3,4],  # Parameters for SMOTE oversampling
    'smote_over__sampling_strategy': [0.1,0.2, 0.3, 0.4,0.5],
    'smote_under__sampling_strategy': [0.3,0.4, 0.5, 0.6],    
    'classifier__max_depth': [10, 50, 100],
          'classifier__criterion' : ["gini", "entropy"],
          'classifier__max_features': ['sqrt','log2',None],
          'smote_over__k_neighbors': [2, 3, 4]}



search = train_model(model,params,refit_score,X_train,y_train)
final_results = evaluate_model ("RF",search, final_results)

/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py:425: FitFailedWarning: 
486 fits failed out of a total of 3240.
The score on these train-test partitions for these parameters will be set to nan.
If these failures are not expected, you can try to debug them by setting error_score='raise'.

Below are more details about the failures:
--------------------------------------------------------------------------------
486 fits failed with the following error:
Traceback (most recent call last):
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/model_selection/_validation.py", line 732, in _fit_and_score
    estimator.fit(X_train, y_train, **fit_params)
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/base.py", line 1151, in wrapper
    return fit_method(estimator, *args, **kwargs)
  File "/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/imblearn/pipeline.py", line 322, in fit
    Xt

In [21]:
# Save your model to a file
best_rf_precision = search.best_estimator_
dump(best_rf_precision, 'best_rf_precision.joblib')

['best_rf_precision.joblib']

In [22]:
final_results

name  PRECISION    RECALL  F1 score  \
0  logistic   0.175676  0.916667  0.216667   
1       SVM   0.410256  0.916667  0.370370   
2        RF   0.333333  0.583333  0.311905   

                                        BestParamsM1  \
0  {'classifier__C': 0.01, 'classifier__penalty':...   
1  {'classifier__C': 20, 'classifier__degree': 4,...   
2  {'classifier__criterion': 'gini', 'classifier_...   

                                        BestParamsM2  \
0  {'classifier__C': 0.001, 'classifier__penalty'...   
1  {'classifier__C': 1, 'classifier__degree': 3, ...   
2  {'classifier__criterion': 'gini', 'classifier_...   

                                        BestParamsM3  
0  {'classifier__C': 0.01, 'classifier__penalty':...  
1  {'classifier__C': 1, 'classifier__degree': 2, ...  
2  {'classifier__criterion': 'gini', 'classifier_...

In [23]:
y_pred = search.best_estimator_.predict(X_test)
# Calculate the accuracy on the test set
test_accuracy = accuracy_score(y_test, y_pred)
print(f'Test Set Accuracy: {test_accuracy * 100:.2f}%')
print("-------------")
# Print the classification report
y_pred = search.predict(X_train)
print(classification_report(y_train, y_train))
cm = confusion_matrix(y_train, y_train)
print("-------------")
# Print the confusion matrix
print("Confusion Matrix - Training set:")
print(cm)


print("-------------")
# Print the classification report
y_pred = search.predict(X_test)
print(classification_report(y_test, y_pred))
cm = confusion_matrix(y_test, y_pred)
print("-------------")
# Print the confusion matrix
print("Confusion Matrix - Testing set:")
print(cm)

Test Set Accuracy: 99.15%
-------------
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      1398
           1       1.00      1.00      1.00        11

    accuracy                           1.00      1409
   macro avg       1.00      1.00      1.00      1409
weighted avg       1.00      1.00      1.00      1409

-------------
Confusion Matrix - Training set:
[[1398    0]
 [   0   11]]
-------------
              precision    recall  f1-score   support

           0       1.00      0.99      1.00       350
           1       0.50      0.67      0.57         3

    accuracy                           0.99       353
   macro avg       0.75      0.83      0.78       353
weighted avg       0.99      0.99      0.99       353

-------------
Confusion Matrix - Testing set:
[[348   2]
 [  1   2]]


### 4.XGBOOST

In [24]:
model = XGBClassifier()
params = {'smote_over__k_neighbors': [2,3,4],  # Parameters for SMOTE oversampling
        'smote_over__sampling_strategy': [0.1,0.2, 0.3, 0.4],
         'smote_under__sampling_strategy': [0.3,0.4, 0.5, 0.6],    
         'classifier__learning_rate' : [0.001,0.05, 0.1],
          'classifier__max_depth': [4,8],
          'classifier__gamma': [0, 0.25, 0.5, 1.0],
          'classifier__alpha' : [0.001, 0.1,1,10],
          'classifier__reg_lambda': [0.5, 1, 5],
          'classifier__booster': ['gbtree', 'gblinear'],
          'smote_over__k_neighbors': [2, 3, 4]}


search = train_model(model,params,refit_score,X_train,y_train)
final_results = evaluate_model ("XGBoost",search, final_results)

/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [21:11:58] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1705650052425/work/src/learner.cc:742: 
Parameters: { "gamma", "max_depth" } are not used.

  warnings.warn(smsg, UserWarning)
/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [21:11:58] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1705650052425/work/src/learner.cc:742: 
Parameters: { "gamma", "max_depth" } are not used.

  warnings.warn(smsg, UserWarning)
/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [21:12:00] WARNING: /home/conda/feedstock_root/build_artifacts/xgboost-split_1705650052425/work/src/learner.cc:742: 
Parameters: { "gamma", "max_depth" } are not used.

  warnings.warn(smsg, UserWarning)
/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/xgboost/core.py:160: UserWarning: [21:12:01] W

KeyboardInterrupt: 

In [1]:
final_results

NameError: name 'final_results' is not defined

In [39]:
best_params = final_results[final_results['name']=='XGBoost']['BestParamsM3']
best_params.values

array([{'classifier__alpha': 0.1, 'classifier__booster': 'gbtree', 'classifier__gamma': 1.0, 'classifier__learning_rate': 0.05, 'classifier__max_depth': 4, 'classifier__reg_lambda': 5, 'smote_over__k_neighbors': 3}],
      dtype=object)

In [ ]:
# Save your model to a file
best_xgbst_precision = search.best_estimator_
dump(best_xgbst_precision, 'best_xgbst_precision.joblib')

In [40]:
best_params.values[0]

{'classifier__alpha': 0.1,
 'classifier__booster': 'gbtree',
 'classifier__gamma': 1.0,
 'classifier__learning_rate': 0.05,
 'classifier__max_depth': 4,
 'classifier__reg_lambda': 5,
 'smote_over__k_neighbors': 3}

In [47]:
# Print the best parameters and score
print('Best parameters: ', search.best_params_)
print('Best score: ', search.best_score_)
# Access the best model
best_model = search.best_estimator_


Best parameters:  {'classifier__alpha': 0.001, 'classifier__booster': 'gblinear', 'classifier__gamma': 0, 'classifier__learning_rate': 0.001, 'classifier__max_depth': 4, 'classifier__reg_lambda': 0.5, 'smote_over__k_neighbors': 3}
Best score:  0.9166666666666666


In [48]:
best_model

Pipeline(steps=[('smote_over',
                 SMOTE(k_neighbors=3, random_state=11, sampling_strategy=0.1)),
                ('smote_under', RandomUnderSampler(sampling_strategy=0.5)),
                ['classifier',
                 XGBClassifier(alpha=0.001, base_score=None, booster='gblinear',
                               callbacks=None, colsample_bylevel=None,
                               colsample_bynode=None, colsample_bytree=None,
                               device=None, early_stopping_rounds=None,
                               enable...
                               feature_types=None, gamma=0, grow_policy=None,
                               importance_type=None,
                               interaction_constraints=None,
                               learning_rate=0.001, max_bin=None,
                               max_cat_threshold=None, max_cat_to_onehot=None,
                               max_delta_step=None, max_depth=4,
                               max_leaves=None, min_child_weight=None,
                               missing=nan, monotone_constraints=None,
                               multi_strategy=None, n_estimators=None,
                               n_jobs=None, num_parallel_tree=None, ...)]])

In [41]:
classifier = XGBClassifier(alpha=0.1, booster = "gbtree",
                           gamma = 1, learning_rate = 0.05,
                           max_depth = 4, reg_lambda = 5)


Test Set Accuracy: 99.15%


In [58]:
y_pred = search.best_estimator_.predict(X_test)
# Calculate the accuracy on the test set
test_accuracy = accuracy_score(y_test, y_pred)
print(f'Test Set Accuracy: {test_accuracy * 100:.2f}%')
print("-------------")
# Print the classification report
y_pred = search.predict(X_test)
print(classification_report(y_test, y_pred))
cm = confusion_matrix(y_test, y_pred)
print("-------------")
# Print the confusion matrix
print("Confusion Matrix:")
print(cm)

Test Set Accuracy: 99.15%
-------------
              precision    recall  f1-score   support

           0       0.99      1.00      1.00       350
           1       0.00      0.00      0.00         3

    accuracy                           0.99       353
   macro avg       0.50      0.50      0.50       353
weighted avg       0.98      0.99      0.99       353

-------------
Confusion Matrix:
[[350   0]
 [  3   0]]


/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/arb399/.conda/envs/ml_env/lib/python3.8/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
